In [165]:
import os
import nltk

In [166]:
#hyperparameters
##Global
batch_size = 64
epsilon = 0.001
##Embedding
embedding_output = 50
vocab_size = 20000
##wordlevel
word_level_hidden_dim = 32
wordcontext_size = 64
##sentencelevel
sentence_level_hidden_dim = 32
sentencecontext_size = 64
##Other hyperparameters: dropout rate/initializations

In [167]:
review_list = []
score_list = []
tag_list = []

In [168]:
stops = set(['br','<','>','/'])

In [169]:
for i in os.listdir('aclImdb/train/pos/'):
    #print(i)
    if i.endswith('.txt'):
        text = open('aclImdb/train/pos/'+i, encoding ='utf8').read()
        sent = nltk.sent_tokenize(text)           
        words = [nltk.word_tokenize(sentence.lower()) for sentence in sent]
        for ind in range(0,len(words)):
            words[ind] = [word for word in words[ind] if word not in stops]
        review_list.append(words)
        score_list.append((i.split('_')[1].split('.')[0]))
        tag_list.append(1)
print('1-done')
for i in os.listdir('aclImdb/train/neg/'):
    #print(i)
    if i.endswith('.txt'):
        text = (open('aclImdb/train/neg/'+i, encoding ='utf8').read())
        sent = nltk.sent_tokenize(text)
        words = [nltk.word_tokenize(sentence.lower()) for sentence in sent]
        for ind in range(0,len(words)):
            words[ind] = [word for word in words[ind] if word not in stops]        
        review_list.append(words)
        score_list.append((i.split('_')[1].split('.')[0]))
        tag_list.append(0)
print('2-done')
for i in os.listdir('aclImdb/test/pos/'):
    #print(i)
    if i.endswith('.txt'):
        text = (open('aclImdb/test/pos/'+i, encoding ='utf8').read())
        sent = nltk.sent_tokenize(text)
        words = [nltk.word_tokenize(sentence.lower()) for sentence in sent]
        for ind in range(0,len(words)):
            words[ind] = [word for word in words[ind] if word not in stops]
        review_list.append(words)
        score_list.append((i.split('_')[1].split('.')[0]))
        tag_list.append(1)
print('3-done')
for i in os.listdir('aclImdb/test/neg/'):
    #print(i)
    if i.endswith('.txt'):
        text = (open('aclImdb/test/neg/'+i, encoding ='utf8').read())
        sent = nltk.sent_tokenize(text)
        words = [nltk.word_tokenize(sentence.lower()) for sentence in sent]
        for ind in range(0,len(words)):
            words[ind] = [word for word in words[ind] if word not in stops]
        review_list.append(words)
        score_list.append((i.split('_')[1].split('.')[0]))
        tag_list.append(0)
print('4-done')
# load the pos/neg training and testing data

1-done
2-done
3-done
4-done


In [6]:
import torch
import torch.nn as nn
from torch.autograd import Variable
import torchvision.datasets as dset
import torchvision.transforms as transforms
import torch.nn.functional as F
import torch.optim as optim
from torch.nn.utils.rnn import pack_padded_sequence,pad_packed_sequence
import random
import pandas as pd
import copy
import collections
import numpy as np
import math

In [7]:
#tag_list = torch.from_numpy(np.array(tag_list)).type(torch.cuda.FloatTensor)
#score_list = torch.from_numpy(np.array(score_list,dtype = int)).type(torch.cuda.FloatTensor)

In [8]:
# class preprocess(object):
#     ##set of replacewords
#     replaceword = {}
#     ##load the stopwords
#     def load_stopwords(stop_word_directory):
#         stopwords = [line.strip() for line in open(stop_word_directory, 'r', encoding='utf-8')]
#         stopwords.append('\n')
#         stopwords.append('\t')
#         stopwords.append('\u3000')##add what needs to be added
#         stopwords.append('\ufeff')
#         stopwords.append('·')
#         stopwords.append('\r\n')
#         return stopwords
#     ##split articles by '。', parse and remove stopwords
#     def split_article(article,use_stopword,stopwords):
#         sentence_list = []
#         if article[-1] == '。':
#             article_list = (article.split('。')[:-1])
#         else:
#             article_list = article.split('。')
#         for x in range(0,len(article_list)):
#             word_list = (jieba.lcut(article_list[x]))
#             if use_stopword:
#                 for word in word_list:
#                     if word in stopwords:
#                         while word in word_list:
#                             word_list.remove(word)
#             sentence_list.append(word_list)
#         return sentence_list
    
    
class tokenizer(object):
    def __init__(self):
        self.total_words = 0
        self.tokenlist = {}
        self.wordcount_list ={}
        self.tokenized_sequences = []
        self.max_sentence_l = 0
        self.max_article_l = 0
    
    ##form dictionary {word:index}
    def form_token(self,newslist): 
        self.tokenlist = {}
        self.total_words = 0
        for article in newslist:
            for sentence in article:
                for word in sentence:
                    if word not in self.tokenlist:
                        self.tokenlist.update({word:self.total_words})
                        self.total_words = self.total_words + 1
                        
    ##form dictionary {word:count(word)}
    def form_wordcount(self,newslist):
        self.wordcount_list = {x:0 for x in self.tokenlist}
        for article in newslist:
            for sentence in article:
                for word in sentence:
                    self.wordcount_list.update({word:(self.wordcount_list[word]+1)})
    
    ##form dictionary {word:index} for the most frequent no_words words, requires wordcount
    ##and updates tokenlist
    def sort_dict(self,no_words):
        sorteddict = dict(sorted(self.wordcount_list.items(),key = lambda t:t[1],reverse = True)[0:no_words])
        i = 1
        for key in sorteddict:
            sorteddict[key] = i
            i = i + 1
        self.tokenlist = sorteddict

 

    ##tokenize the articles, requires tokenlist
    def tokenize(self,newslist):
        tokenized_newslist = copy.deepcopy(newslist)
        copylist = []
        for article in tokenized_newslist:
            article_list = []
            for i in range(0,len(article)):
                dumsen = []
                for word in article[i]:
                    if (word in self.tokenlist):
                        dumsen.append(self.tokenlist[word])
                if len(dumsen) >= 3:
                    article_list.append(dumsen)
            copylist.append(article_list)
        self.tokenized_sequences = copylist
        
    def add_count_position(self):

        for i in range(0,len(self.tokenized_sequences)):
            for j in range(0,len(self.tokenized_sequences[i])):
                self.tokenized_sequences[i][j].insert(0,min(len(self.tokenized_sequences[i][j]),self.max_sentence_l))
                self.tokenized_sequences[i][j].insert(0,min(len(self.tokenized_sequences[i]),self.max_article_l))
                self.tokenized_sequences[i][j].insert(0,i)


    #set max lengths (of articles and sentences) as the maximum lengths from the sample
    def use_max_l(self):
        max_sentence_l = 0
        max_article_l = 0
        for article in self.tokenized_sequences:
            if len(article) > max_article_l:
                max_article_l = len(article)
            for sentence in article:
                if len(sentence) > max_sentence_l:
                    max_sentence_l = len(sentence)
        self.max_sentence_l = max_sentence_l
        self.max_article_l = max_article_l

    ##set max lengths (of articles and sentences) as factor*average lengths from the sample
    def use_avg_l(self,factor):
        tot_sentence_l = 0
        tot_article_l = 0
        tot_sentences = 0
        tot_articles = 0
        for article in self.tokenized_sequences:
            tot_article_l = len(article) + tot_article_l
            tot_articles = tot_articles + 1
            for sentence in article:
                tot_sentence_l = len(sentence) + tot_sentence_l
                tot_sentences = tot_sentences + 1
        if tot_sentences != 0:
            self.max_sentence_l = math.floor((tot_sentence_l/tot_sentences)*factor)
            self.max_article_l = math.floor((tot_article_l/tot_articles)*factor)
        else:
            print('Error: No article')
            
    ##pad the sentences into the form (batch,article_length,max_sentence_length)
    def padsentence(self):
        for article in self.tokenized_sequences:
            for i in range(0,len(article)):
                
                if len(article[i]) < self.max_sentence_l+3:
                    while len(article[i]) < self.max_sentence_l+3:
                        article[i].append(0)
                else:
                    dumsen = []
                    for j in range(0,self.max_sentence_l+3):
                        dumsen.append(article[i][j])
                    article[i] = dumsen
                    
    ##pad the sentences into the form (batch,max_article_length,sentence_length)                   
    def padarticle(self):
        for i in range(0,len(self.tokenized_sequences)):
            if len(self.tokenized_sequences[i]) < self.max_article_l:
                while len(self.tokenized_sequences[i]) < self.max_article_l:
                    (self.tokenized_sequences[i]).append(list(np.zeros(shape = self.max_sentence_l,dtype=int)))
            else:
                dumart = []
                for j in range(0,self.max_article_l):
                    dumart.append(self.tokenized_sequences[i][j]) 
                self.tokenized_sequences[i] = dumart

In [170]:
tok  = tokenizer()
tok.form_token(review_list)
tok.form_wordcount(review_list)
tok.sort_dict(vocab_size)
tok.tokenize(review_list)
tok.use_avg_l(1.8)
tok.add_count_position()
tok.padsentence()

In [171]:
review_list

[[['for',
   'a',
   'movie',
   'that',
   'gets',
   'no',
   'respect',
   'there',
   'sure',
   'are',
   'a',
   'lot',
   'of',
   'memorable',
   'quotes',
   'listed',
   'for',
   'this',
   'gem',
   '.'],
  ['imagine',
   'a',
   'movie',
   'where',
   'joe',
   'piscopo',
   'is',
   'actually',
   'funny',
   '!'],
  ['maureen', 'stapleton', 'is', 'a', 'scene', 'stealer', '.'],
  ['the', 'moroni', 'character', 'is', 'an', 'absolute', 'scream', '.'],
  ['watch',
   'for',
   'alan',
   '``',
   'the',
   'skipper',
   "''",
   'hale',
   'jr.',
   'as',
   'a',
   'police',
   'sgt',
   '.']],
 [['bizarre',
   'horror',
   'movie',
   'filled',
   'with',
   'famous',
   'faces',
   'but',
   'stolen',
   'by',
   'cristina',
   'raines',
   '(',
   'later',
   'of',
   'tv',
   "'s",
   '``',
   'flamingo',
   'road',
   "''",
   ')',
   'as',
   'a',
   'pretty',
   'but',
   'somewhat',
   'unstable',
   'model',
   'with',
   'a',
   'gummy',
   'smile',
   'who',
   

In [172]:
emb = (line.strip() for line in open('glove.6B.'+str(embedding_output)+'d.txt', 'r', encoding='utf-8'))

In [173]:
embedding = {}
for x in emb:
    embedding.update({x.split(' ',1)[0]:x.split(' ',1)[1]})

##turn embedding into tensor
for x in embedding:
    strarray = embedding[x].split(' ')
    array = np.array(list(map(float,strarray)))
    embedding[x] = array

In [174]:
correspond = {}
for x in tok.tokenlist:
    if x in embedding:
        correspond.update({tok.tokenlist[x]:torch.from_numpy(embedding[x]).type(torch.FloatTensor)})

In [175]:
emb_mat = torch.zeros((1,embedding_output)).type(torch.FloatTensor)
for i in range(1,vocab_size+1):
    if i in correspond:
        emb_mat = torch.cat((emb_mat,correspond[i].unsqueeze(0)),dim = 0)
    else:
        r = torch.randn((1,embedding_output)).type(torch.FloatTensor)
        emb_mat = torch.cat((emb_mat,r/r.norm()),dim = 0)
del emb
del embedding
del correspond

In [176]:
from matplotlib import pyplot as plt 
import matplotlib

In [177]:
class sentence_level_net(nn.Module):
    def __init__(self):
        super(sentence_level_net,self).__init__()
        self.rnn = nn.GRU
        self.sec2doc = self.rnn(input_size= word_level_hidden_dim*2,
                                 hidden_size = sentence_level_hidden_dim,
                                 bias = True,
                                 batch_first = True, 
                                 bidirectional = True
                                )
        
        torch.nn.init.orthogonal_(self.sec2doc.weight_ih_l0)
        torch.nn.init.orthogonal_(self.sec2doc.weight_hh_l0)
        torch.nn.init.orthogonal_(self.sec2doc.weight_ih_l0_reverse)
        torch.nn.init.orthogonal_(self.sec2doc.weight_hh_l0_reverse)
        torch.nn.init.constant_(self.sec2doc.bias_ih_l0,1)
        torch.nn.init.constant_(self.sec2doc.bias_hh_l0,1)
        torch.nn.init.constant_(self.sec2doc.bias_ih_l0_reverse,1)
        torch.nn.init.constant_(self.sec2doc.bias_ih_l0_reverse,1)
        
        self.sentencecontext = nn.Parameter(torch.FloatTensor(sentencecontext_size,1))
        torch.nn.init.normal_(self.sentencecontext,mean = 0, std = 1)
        self.projection = nn.Linear(sentence_level_hidden_dim*2,sentencecontext_size,bias=True)
        self.projection_activ = nn.Tanh()
        self.fc1 = nn.Linear(sentence_level_hidden_dim*2,10)
        self.dropout = nn.Dropout(p=0.5)
    def forward(self,x,lengths):
        batch_size= len(x)
        ##sort
        sort,order = torch.sort(lengths,descending = True)
        _,back_order = torch.sort(order,descending = False)
        ##pack
        o = pack_padded_sequence(x[order],sort,batch_first= True)
        ##RNN
        o,_ = self.sec2doc(o)
        ##unpack
        o = pad_packed_sequence(o,batch_first=True)
        ##unsort
        o = o[0][back_order]
        ##create mask
        mask = (o.norm(dim=2) != 0 ).type(torch.FloatTensor).unsqueeze(2)
        mask.requires_grad = False
        ##projection and similarity
        o_1 = self.projection(o)
        o_1 = self.dropout(o_1)
        o_1= self.projection_activ(o_1).view(-1,sentencecontext_size)
        o_1 = (torch.mm(o_1,self.sentencecontext)).view(batch_size,-1,1)
        ##masked Softmax
        o_1 = torch.exp(o_1)
        o_1 = o_1*mask
        o_1 = o_1/(torch.sum(o_1,dim = 1,keepdim = True)+epsilon)
        o = o*o_1
        o = (torch.sum(o,dim=1,keepdim=False))
        ##Dense and output
        o = (self.fc1(o))
        return o
    
    
class word_level_net(nn.Module):
    def __init__(self):
        super(word_level_net,self).__init__()
        
        self.embedding = nn.Embedding(num_embeddings = vocab_size+1,embedding_dim = embedding_output,padding_idx=0)
        self.embedding.weight.data.copy_(emb_mat)
        self.embedding.weight.requires_grad = False
        #self.embedding = nn.Embedding.from_pretrained(emb_mat)
        self.rnn = nn.GRU
        self.word2sen = self.rnn(input_size= embedding_output,
                                 hidden_size = word_level_hidden_dim,
                                 bias = True,
                                 batch_first = True, 
                                 bidirectional = True
                                )
        
        torch.nn.init.orthogonal_(self.word2sen.weight_ih_l0)
        torch.nn.init.orthogonal_(self.word2sen.weight_hh_l0)
        torch.nn.init.orthogonal_(self.word2sen.weight_ih_l0_reverse)
        torch.nn.init.orthogonal_(self.word2sen.weight_hh_l0_reverse)
        torch.nn.init.constant_(self.word2sen.bias_ih_l0,1)
        torch.nn.init.constant_(self.word2sen.bias_hh_l0,1)
        torch.nn.init.constant_(self.word2sen.bias_ih_l0_reverse,1)
        torch.nn.init.constant_(self.word2sen.bias_ih_l0_reverse,1)
        
        self.wordcontext = nn.Parameter(torch.FloatTensor(wordcontext_size,1))
        torch.nn.init.normal_(self.wordcontext,mean = 0, std = 1)
        self.projection = nn.Linear(word_level_hidden_dim*2,wordcontext_size,bias=True)
        self.projection_activ = nn.Tanh()          
        self.dropout = nn.Dropout(p=0.5)
        
    def forward(self,x,lengths,tokenizer = tok):
        batch_size = len(x)
        sort,order_by_length = torch.sort(lengths[:,2],dim=0,descending = True)
        _,backorder_by_length = torch.sort(order_by_length,dim=0,descending = False)
        o = x[order_by_length]
        ##Embedding(Requires torch.cuda.longtensor)
        o  = o.type(torch.LongTensor)        
        o = self.embedding(o)
        ##pack
        o = pack_padded_sequence(o,sort,batch_first=True)
        ##RNN
   
        o,_ = self.word2sen(o)
        ##unpack       
        o = pad_packed_sequence(o,batch_first=True)
    
        ##unsort the sequences
        o = o[0][backorder_by_length]
        ##clone and create mask      
        mask = (o.norm(dim=2) != 0 ).type(torch.FloatTensor).unsqueeze(2)
        ##project and similarity
        o_1 = self.projection(o)
        print(o_1.size())
        o_1 = self.dropout(o_1)
        o_1 = (self.projection_activ(o_1)).view(-1,wordcontext_size)
        print(o_1.size())
        o_1 = (torch.mm(o_1,self.wordcontext)).view(batch_size,-1,1)
        print(o_1.size())
        ##maskedsoftmax
        o_1 = torch.exp(o_1)
        o_1 = o_1*mask
        o_1 = o_1/(torch.sum(o_1,dim = 1,keepdim = True)+epsilon)
        print(o_1.size())
        o = o*o_1
        ##sum up
        o = torch.sum(o,dim=1)
        return lengths,o

class HAN(nn.Module):
    def __init__(self):
        super(HAN,self).__init__()
        self.WLN = word_level_net()
        self.SLN = sentence_level_net()
    def forward(self,x,lengths):
        index,output = self.WLN(x,lengths)
        change_article_index = []
        change_article_index.append(0)
        article_length_index = []

        for i in range(0,len(index[:,0])-1):
            if index[:,0][i] != index[:,0][i+1]:
                change_article_index.append(i+1)
        for j in range(0,len(change_article_index)-1):
            article_length_index.append(change_article_index[j+1]-
                                        change_article_index[j])
        article_length_index.append(len(index[:,0])-change_article_index[len(change_article_index)-1])
        
        ##pad each batch into a tensor
        print(article_length_index)
        if article_length_index[0] >= tok.max_article_l:
            batch_articles = (output[change_article_index[0]:change_article_index[0]+tok.max_article_l]).unsqueeze(0)
        else:
            pad = torch.nn.ConstantPad2d((0,0,0,tok.max_article_l-article_length_index[0]),0)
            batch_articles = (pad(output[change_article_index[0]:change_article_index[1]])).unsqueeze(0)



        for i in range(1,len(article_length_index)):
            if article_length_index[i] >= tok.max_article_l:
                this_article = (output[change_article_index[i]:change_article_index[i]+tok.max_article_l].unsqueeze(0))
                batch_articles = torch.cat((batch_articles,this_article),
                                          dim = 0)
            else:
                if i == (len(article_length_index)-1):
                    pad = torch.nn.ConstantPad2d((0,0,0,tok.max_article_l-article_length_index[i]),0)
                    this_article = (pad(output[change_article_index[i]:len(index[:,0])])).unsqueeze(0)
                    batch_articles = torch.cat((batch_articles,this_article),dim=0)
                else:
                    pad = torch.nn.ConstantPad2d((0,0,0,tok.max_article_l-article_length_index[i]),0)
                    this_article = (pad(output[change_article_index[i]:change_article_index[i+1]])).unsqueeze(0)      
                    batch_articles = torch.cat((batch_articles,this_article),dim=0)

        article_length_index = torch.IntTensor(article_length_index)


        for i in range(0,len(article_length_index)):
            article_length_index[i] = min(article_length_index[i],tok.max_article_l)
        
        output = self.SLN(batch_articles,article_length_index)
        return(output)

In [178]:
X = copy.deepcopy(tok.tokenized_sequences)
Y  = [int(i) for i in score_list]
seed =  random.randint(0,5000)
print('seed = '+str(seed))
random.seed(seed)
Z = list(zip(X,Y))
random.shuffle(Z)
X[:],Y[:] = zip(*Z)
X_train = X[0:math.floor(0.5*len(X))]
X_test = X[math.floor(0.95*len(X)):len(X)]
Y_train = Y[0:math.floor(0.5*len(Y))]
Y_test = Y[math.floor(0.95*len(Y)):len(Y)]
#len_list = ([min(len(X_train[i]),tok.max_sentence_l) for i in range(0,len(X_train))])
#dummy,myorder = torch.sort(torch.from_numpy(np.array(len_list)),descending= False)
#X_train = [X_train[i] for i in myorder]
#Y_train = [Y_train[i] for i in myorder]
Y_test_tensor = (torch.from_numpy(np.array(Y_test))-1).type(torch.LongTensor)
Y_train_tensor = (torch.from_numpy(np.array(Y_train))-1).type(torch.LongTensor)
print(type(X),type(Y))

seed = 3906
<class 'list'> <class 'list'>


In [179]:
print(X[1][0])
print(X[1][1])

[39971, 8, 7, 12, 225, 8, 4459, 4, 360, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[39971, 8, 15, 1, 690, 30, 1, 177, 161, 180, 1239, 2, 331, 17, 1045, 7225, 2934, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]


In [180]:
H = HAN()
lossfun = torch.nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(H.parameters(),lr = 1e-3 , weight_decay = 0.003)

In [181]:
train_loss = []
test_loss = []
test_acc = []

In [182]:
def go(epoch):
    for epoch in range(0,epoch):
        print('epoch ' + str(epoch))
        ##shuffle train
        max_batch = math.floor(len(X_train)/batch_size)
        seed =  random.randint(0,5000)
        print('seed = '+ str(seed))
        random.seed(seed)
        randomizer = list(range(max_batch))
        #print(randomizer)
        random.shuffle(randomizer)
        ##Batch Training
        print('Training...')
        batch_idx = 0
        loss_list = []
        while (batch_idx+1)*batch_size < len(X_train):
            #print('batch '+str(batch_idx))
            optimizer.zero_grad()
            tok_seqn_w_count = []
            
            #print(batch_idx,randomizer[batch_idx])
            batch_target = X_train[randomizer[batch_idx]*batch_size:randomizer[batch_idx]*batch_size+batch_size]

            for article in batch_target:
                for sentence in article:
                    tok_seqn_w_count.append(sentence)

            batch = torch.from_numpy(np.array(tok_seqn_w_count))
            batch_articles = batch[:,3:]
            batch_ind = batch[:,0:3]
            batch_ar = Variable(batch_articles)
            target = Variable(Y_train_tensor[randomizer[batch_idx]*batch_size:randomizer[batch_idx]*batch_size+batch_size])

            #forward pass
            output = H(batch_ar,batch_ind)
            ##loss calculation
            loss = lossfun(output,target)
            loss_list.append(loss.item())
            ##backward pass
            loss.backward()
            optimizer.step()
            #print('loss = ' + str(loss.item()))
            batch_idx = batch_idx + 1


        ##Testing
        train_loss.append(round(np.mean(loss_list),5))
        print('Training Loss = '+str(round(np.mean(loss_list),5)))
        print('Validating...')
        tok_seqn_w_count = []
        batch_target = X_test

        for article in X_test:
            for sentence in article:
                tok_seqn_w_count.append(sentence)

        batch = torch.from_numpy(np.array(tok_seqn_w_count))
        batch_articles = batch[:,3:]
        batch_ind = batch[:,0:3]
        batch = Variable(batch_articles)

        target = Variable(Y_test_tensor)
        output = H(batch_articles,batch_ind).squeeze(1)

        loss = lossfun(output,target)
        ##accuarcy
        q = torch.argmax(output,dim=1)
        countvague = 0
        count = 0
        for i in range(0,len(q)):
            if abs(q[i] - target[i])==0:
                count = count + 1
            if abs(q[i] - target[i])<=1:
                countvague = countvague + 1
        accuracy = round(count/len(output),5)*100
        accvague = round(countvague/len(output),5)*100
        test_loss.append(loss.item())
        test_acc.append(accuracy)
        print('Validation Loss = ' + str(loss.item()))
        print('Validation Accuarcy = ' + str(accuracy) +' %')
        print('% Almost Correct  = ' + str(accvague) +' %')
    

In [164]:
go(15)
H.WLN.embedding.weight.requires_grad = True
go(10)

epoch 0
seed = 3416
Training...
torch.Size([680, 43, 64])
torch.Size([29240, 64])
torch.Size([680, 43, 1])
torch.Size([680, 43, 1])
[9, 6, 8, 4, 13, 10, 14, 17, 6, 4, 10, 16, 8, 15, 6, 8, 9, 11, 2, 6, 16, 24, 6, 19, 2, 11, 8, 9, 10, 5, 13, 56, 3, 7, 6, 6, 11, 11, 1, 9, 15, 43, 15, 10, 2, 9, 12, 12, 16, 8, 7, 13, 5, 1, 22, 5, 7, 12, 9, 11, 12, 8, 9, 2]
torch.Size([715, 43, 64])
torch.Size([30745, 64])
torch.Size([715, 43, 1])
torch.Size([715, 43, 1])
[11, 19, 26, 6, 14, 9, 14, 8, 6, 11, 8, 12, 4, 11, 10, 6, 23, 7, 13, 12, 15, 11, 14, 12, 15, 10, 4, 51, 5, 9, 7, 9, 6, 8, 5, 7, 13, 20, 13, 17, 11, 4, 14, 10, 9, 8, 13, 13, 10, 17, 6, 8, 8, 7, 19, 7, 4, 23, 10, 4, 4, 2, 18, 5]
torch.Size([618, 43, 64])
torch.Size([26574, 64])
torch.Size([618, 43, 1])
torch.Size([618, 43, 1])
[8, 6, 14, 6, 4, 13, 15, 4, 5, 10, 11, 11, 6, 1, 46, 14, 9, 10, 4, 8, 4, 16, 7, 16, 9, 9, 5, 7, 13, 5, 3, 4, 7, 17, 7, 31, 8, 15, 11, 8, 11, 11, 10, 11, 16, 6, 6, 8, 13, 7, 8, 1, 21, 15, 11, 6, 1, 11, 6, 9, 8, 5, 5, 5]


KeyboardInterrupt: 